Experimenting xgboost Fine Tuning with housing prices's kaggle competition dataset.

Stacking models implementation is intended to be done in the future.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import train_test_split
from xgboost import XGBRegressor


Data Preprocessing step

In [2]:
# Read the data
x_full = pd.read_csv('train.csv', index_col='Id')
X_test_full = pd.read_csv('test.csv', index_col='Id')

# Remove rows with missing target, separate target from predictors
x_full.dropna(axis=0, subset=['SalePrice'], inplace=True)
y = x_full.SalePrice
x_full.drop(['SalePrice'], axis=1, inplace=True)

# Break off validation set from training data
X_train_full, X_valid_full, y_train, y_valid = train_test_split(x_full, y, 
                                                                train_size=0.8, test_size=0.2,
                                                                random_state=0)

# "Cardinality" means the number of unique values in a column
# Select categorical columns with relatively low cardinality (convenient but arbitrary)
categorical_cols = [cname for cname in X_train_full.columns if
                    #X_train_full[cname].nunique() < 20 and 
                    X_train_full[cname].dtype == "object"]

# Select numerical columns
numerical_cols = [cname for cname in X_train_full.columns if 
                X_train_full[cname].dtype in ['int64', 'float64']]

# Keep selected columns only
cols = categorical_cols + numerical_cols
X_train = X_train_full[cols].copy()
X_valid = X_valid_full[cols].copy()
X_test = X_test_full[cols].copy()
x_full_2 = x_full[cols].copy()


In [3]:
X_train.head()

MSZoning Street Alley LotShape LandContour Utilities LotConfig LandSlope  \
Id                                                                             
619       RL   Pave   NaN      Reg         Lvl    AllPub    Inside       Gtl   
871       RL   Pave   NaN      Reg         Lvl    AllPub    Inside       Gtl   
93        RL   Pave  Grvl      IR1         HLS    AllPub    Inside       Gtl   
818       RL   Pave   NaN      IR1         Lvl    AllPub   CulDSac       Gtl   
303       RL   Pave   NaN      IR1         Lvl    AllPub    Corner       Gtl   

    Neighborhood Condition1  ... GarageArea WoodDeckSF OpenPorchSF  \
Id                           ...                                     
619      NridgHt       Norm  ...        774          0         108   
871        NAmes       PosN  ...        308          0           0   
93       Crawfor       Norm  ...        432          0           0   
818      Mitchel       Norm  ...        857        150          59   
303      CollgCr       Norm  ...        843        468          81   

    EnclosedPorch 3SsnPorch ScreenPorch PoolArea MiscVal MoSold YrSold  
Id                                                                      
619             0         0         260        0       0      7   2007  
871             0         0           0        0       0      8   2009  
93             44         0           0        0       0      8   2009  
818             0         0           0        0       0      7   2008  
303             0         0           0        0       0      1   2006  

[5 rows x 79 columns]

In [28]:
#dealing with missing values (numerical variables)
numerical_imputer = SimpleImputer(strategy='median')
numerical_X_train = X_train[numerical_cols].copy()
numerical_X_valid = X_valid[numerical_cols].copy()
numerical_X_test = X_test[numerical_cols].copy()

imputed_numerical_X_train = pd.DataFrame(numerical_imputer.fit_transform(numerical_X_train))
imputed_numerical_X_valid = pd.DataFrame(numerical_imputer.transform(numerical_X_valid))
imputed_numerical_X_test = pd.DataFrame(numerical_imputer.transform(numerical_X_test))

imputed_numerical_X_train.columns = numerical_X_train.columns
imputed_numerical_X_valid.columns = numerical_X_valid.columns
imputed_numerical_X_test.columns = numerical_X_test.columns

In [5]:
imputed_numerical_X_train.head()

MSSubClass  LotFrontage  LotArea  OverallQual  OverallCond  YearBuilt  \
0        20.0         90.0  11694.0          9.0          5.0     2007.0   
1        20.0         60.0   6600.0          5.0          5.0     1962.0   
2        30.0         80.0  13360.0          5.0          7.0     1921.0   
3        20.0         69.0  13265.0          8.0          5.0     2002.0   
4        20.0        118.0  13704.0          7.0          5.0     2001.0   

   YearRemodAdd  MasVnrArea  BsmtFinSF1  BsmtFinSF2  ...  GarageArea  \
0        2007.0       452.0        48.0         0.0  ...       774.0   
1        1962.0         0.0         0.0         0.0  ...       308.0   
2        2006.0         0.0       713.0         0.0  ...       432.0   
3        2002.0       148.0      1218.0         0.0  ...       857.0   
4        2002.0       150.0         0.0         0.0  ...       843.0   

   WoodDeckSF  OpenPorchSF  EnclosedPorch  3SsnPorch  ScreenPorch  PoolArea  \
0         0.0        108.0            0.0        0.0        260.0       0.0   
1         0.0          0.0            0.0        0.0          0.0       0.0   
2         0.0          0.0           44.0        0.0          0.0       0.0   
3       150.0         59.0            0.0        0.0          0.0       0.0   
4       468.0         81.0            0.0        0.0          0.0       0.0   

   MiscVal  MoSold  YrSold  
0      0.0     7.0  2007.0  
1      0.0     8.0  2009.0  
2      0.0     8.0  2009.0  
3      0.0     7.0  2008.0  
4      0.0     1.0  2006.0  

[5 rows x 36 columns]

In [30]:
#dealing with missing values (categorical variables)
categorical_imputer = SimpleImputer(strategy='most_frequent')
categorical_X_train = X_train[categorical_cols].copy()
categorical_X_valid = X_valid[categorical_cols].copy()
categorical_X_test = X_test[categorical_cols].copy()

imputed_categorical_X_train=pd.DataFrame(categorical_imputer.fit_transform(categorical_X_train))
imputed_categorical_X_valid=pd.DataFrame(categorical_imputer.transform(categorical_X_valid))
imputed_categorical_X_test=pd.DataFrame(categorical_imputer.transform(categorical_X_test))


imputed_categorical_X_train.columns = categorical_X_train.columns
imputed_categorical_X_valid.columns = categorical_X_valid.columns
imputed_categorical_X_test.columns = categorical_X_test.columns

In [7]:
imputed_categorical_X_train.head()

MSZoning Street Alley LotShape LandContour Utilities LotConfig LandSlope  \
0       RL   Pave  Grvl      Reg         Lvl    AllPub    Inside       Gtl   
1       RL   Pave  Grvl      Reg         Lvl    AllPub    Inside       Gtl   
2       RL   Pave  Grvl      IR1         HLS    AllPub    Inside       Gtl   
3       RL   Pave  Grvl      IR1         Lvl    AllPub   CulDSac       Gtl   
4       RL   Pave  Grvl      IR1         Lvl    AllPub    Corner       Gtl   

  Neighborhood Condition1  ... GarageType GarageFinish GarageQual GarageCond  \
0      NridgHt       Norm  ...     Attchd          Unf         TA         TA   
1        NAmes       PosN  ...     Detchd          Unf         TA         TA   
2      Crawfor       Norm  ...     Detchd          Unf         TA         TA   
3      Mitchel       Norm  ...     Attchd          RFn         TA         TA   
4      CollgCr       Norm  ...     Attchd          RFn         TA         TA   

  PavedDrive PoolQC  Fence MiscFeature SaleType SaleCondition  
0          Y     Gd  MnPrv        Shed      New       Partial  
1          Y     Gd  MnPrv        Shed       WD        Normal  
2          Y     Gd  MnPrv        Shed       WD        Normal  
3          Y     Gd  MnPrv        Shed       WD        Normal  
4          Y     Gd  MnPrv        Shed       WD        Normal  

[5 rows x 43 columns]

In [31]:
#converting categorical variables to numbers with OneHotEncoder
oh_encoder = OneHotEncoder(handle_unknown='ignore', sparse=False)
oh_cols_train = pd.DataFrame(oh_encoder.fit_transform(imputed_categorical_X_train))
oh_cols_valid = pd.DataFrame(oh_encoder.transform(imputed_categorical_X_valid))
oh_cols_test = pd.DataFrame(oh_encoder.transform(imputed_categorical_X_test))

oh_cols_train.index = imputed_categorical_X_train.index
oh_cols_valid.index = imputed_categorical_X_valid.index
oh_cols_test.index = imputed_categorical_X_test.index

clean_X_train = pd.concat([imputed_numerical_X_train, oh_cols_train], axis=1)
clean_X_valid = pd.concat([imputed_numerical_X_valid, oh_cols_valid], axis=1)
clean_X_test = pd.concat([imputed_numerical_X_test, oh_cols_test], axis=1)

In [9]:
clean_X_train.head()

MSSubClass  LotFrontage  LotArea  OverallQual  OverallCond  YearBuilt  \
0        20.0         90.0  11694.0          9.0          5.0     2007.0   
1        20.0         60.0   6600.0          5.0          5.0     1962.0   
2        30.0         80.0  13360.0          5.0          7.0     1921.0   
3        20.0         69.0  13265.0          8.0          5.0     2002.0   
4        20.0        118.0  13704.0          7.0          5.0     2001.0   

   YearRemodAdd  MasVnrArea  BsmtFinSF1  BsmtFinSF2  ...  237  238  239  240  \
0        2007.0       452.0        48.0         0.0  ...  0.0  1.0  0.0  0.0   
1        1962.0         0.0         0.0         0.0  ...  0.0  0.0  0.0  1.0   
2        2006.0         0.0       713.0         0.0  ...  0.0  0.0  0.0  1.0   
3        2002.0       148.0      1218.0         0.0  ...  0.0  0.0  0.0  1.0   
4        2002.0       150.0         0.0         0.0  ...  0.0  0.0  0.0  1.0   

   241  242  243  244  245  246  
0  0.0  0.0  0.0  0.0  0.0  1.0  
1  0.0  0.0  0.0  0.0  1.0  0.0  
2  0.0  0.0  0.0  0.0  1.0  0.0  
3  0.0  0.0  0.0  0.0  1.0  0.0  
4  0.0  0.0  0.0  0.0  1.0  0.0  

[5 rows x 283 columns]

In [34]:
clean_X_test.head()

MSSubClass  LotFrontage  LotArea  OverallQual  OverallCond  YearBuilt  \
0        20.0         80.0  11622.0          5.0          6.0     1961.0   
1        20.0         81.0  14267.0          6.0          6.0     1958.0   
2        60.0         74.0  13830.0          5.0          5.0     1997.0   
3        60.0         78.0   9978.0          6.0          6.0     1998.0   
4       120.0         43.0   5005.0          8.0          5.0     1992.0   

   YearRemodAdd  MasVnrArea  BsmtFinSF1  BsmtFinSF2  ...  237  238  239  240  \
0        1961.0         0.0       468.0       144.0  ...  0.0  0.0  0.0  1.0   
1        1958.0       108.0       923.0         0.0  ...  0.0  0.0  0.0  1.0   
2        1998.0         0.0       791.0         0.0  ...  0.0  0.0  0.0  1.0   
3        1998.0        20.0       602.0         0.0  ...  0.0  0.0  0.0  1.0   
4        1992.0         0.0       263.0         0.0  ...  0.0  0.0  0.0  1.0   

   241  242  243  244  245  246  
0  0.0  0.0  0.0  0.0  1.0  0.0  
1  0.0  0.0  0.0  0.0  1.0  0.0  
2  0.0  0.0  0.0  0.0  1.0  0.0  
3  0.0  0.0  0.0  0.0  1.0  0.0  
4  0.0  0.0  0.0  0.0  1.0  0.0  

[5 rows x 283 columns]

Time to define the model

In [26]:
%%time
#defining arbitrary hyperparameters to tune it later
xgb = XGBRegressor(n_estimators=100000, learning_rate=0.001, max_depth=4, subsample=0.5, 
                  colsample_bytree=0.5, colsample_bylevel=0.6, colsample_bynode=0.5)

xgb.fit(clean_X_train, y_train, early_stopping_rounds=50000, eval_set=[(clean_X_valid, y_valid)],
        eval_metric = 'mae')
preds = xgb.predict(clean_X_valid)
print('MAE: ', mean_absolute_error(y_valid, preds))

[0]	validation_0-mae:181191.06250
Will train until validation_0-mae hasn't improved in 50000 rounds.
[1]	validation_0-mae:181020.34375
[2]	validation_0-mae:180845.43750
[3]	validation_0-mae:180672.65625
[4]	validation_0-mae:180494.60938
[5]	validation_0-mae:180320.60938
[6]	validation_0-mae:180145.59375
[7]	validation_0-mae:179966.50000
[8]	validation_0-mae:179788.07812
[9]	validation_0-mae:179610.06250
[10]	validation_0-mae:179432.31250
[11]	validation_0-mae:179258.65625
[12]	validation_0-mae:179083.25000
[13]	validation_0-mae:178904.17188
[14]	validation_0-mae:178739.32812
[15]	validation_0-mae:178567.06250
[16]	validation_0-mae:178394.93750
[17]	validation_0-mae:178217.18750
[18]	validation_0-mae:178039.21875
[19]	validation_0-mae:177863.92188
[20]	validation_0-mae:177688.29688
[21]	validation_0-mae:177512.07812
[22]	validation_0-mae:177338.18750
[23]	validation_0-mae:177166.39062
[24]	validation_0-mae:176987.45312
[25]	validation_0-mae:176812.71875
[26]	validation_0-mae:176634.0468

[229]	validation_0-mae:144813.28125
[230]	validation_0-mae:144669.43750
[231]	validation_0-mae:144529.39062
[232]	validation_0-mae:144386.70312
[233]	validation_0-mae:144243.39062
[234]	validation_0-mae:144101.59375
[235]	validation_0-mae:143957.17188
[236]	validation_0-mae:143818.01562
[237]	validation_0-mae:143676.34375
[238]	validation_0-mae:143535.96875
[239]	validation_0-mae:143396.93750
[240]	validation_0-mae:143258.03125
[241]	validation_0-mae:143121.78125
[242]	validation_0-mae:142980.00000
[243]	validation_0-mae:142840.57812
[244]	validation_0-mae:142697.65625
[245]	validation_0-mae:142556.64062
[246]	validation_0-mae:142419.78125
[247]	validation_0-mae:142279.20312
[248]	validation_0-mae:142136.65625
[249]	validation_0-mae:141993.54688
[250]	validation_0-mae:141853.62500
[251]	validation_0-mae:141712.50000
[252]	validation_0-mae:141572.76562
[253]	validation_0-mae:141435.09375
[254]	validation_0-mae:141297.28125
[255]	validation_0-mae:141160.26562
[256]	validation_0-mae:14102

[457]	validation_0-mae:115939.61719
[458]	validation_0-mae:115827.16406
[459]	validation_0-mae:115712.07031
[460]	validation_0-mae:115605.17969
[461]	validation_0-mae:115491.42188
[462]	validation_0-mae:115374.25000
[463]	validation_0-mae:115265.12500
[464]	validation_0-mae:115153.09375
[465]	validation_0-mae:115040.96875
[466]	validation_0-mae:114927.91406
[467]	validation_0-mae:114814.39844
[468]	validation_0-mae:114702.40625
[469]	validation_0-mae:114592.65625
[470]	validation_0-mae:114483.31250
[471]	validation_0-mae:114374.07812
[472]	validation_0-mae:114261.10156
[473]	validation_0-mae:114148.40625
[474]	validation_0-mae:114033.05469
[475]	validation_0-mae:113923.89844
[476]	validation_0-mae:113815.55469
[477]	validation_0-mae:113699.23438
[478]	validation_0-mae:113589.33594
[479]	validation_0-mae:113478.41406
[480]	validation_0-mae:113371.97656
[481]	validation_0-mae:113262.25000
[482]	validation_0-mae:113151.63281
[483]	validation_0-mae:113041.91406
[484]	validation_0-mae:11293

[687]	validation_0-mae:92785.71094
[688]	validation_0-mae:92696.79688
[689]	validation_0-mae:92607.38281
[690]	validation_0-mae:92517.76562
[691]	validation_0-mae:92426.25781
[692]	validation_0-mae:92337.82812
[693]	validation_0-mae:92252.45312
[694]	validation_0-mae:92164.63281
[695]	validation_0-mae:92073.78125
[696]	validation_0-mae:91986.42969
[697]	validation_0-mae:91897.45312
[698]	validation_0-mae:91807.13281
[699]	validation_0-mae:91720.02344
[700]	validation_0-mae:91632.92188
[701]	validation_0-mae:91546.91406
[702]	validation_0-mae:91456.80469
[703]	validation_0-mae:91366.88281
[704]	validation_0-mae:91282.18750
[705]	validation_0-mae:91194.25000
[706]	validation_0-mae:91107.94531
[707]	validation_0-mae:91021.17188
[708]	validation_0-mae:90936.53125
[709]	validation_0-mae:90847.68750
[710]	validation_0-mae:90759.63281
[711]	validation_0-mae:90670.00781
[712]	validation_0-mae:90583.19531
[713]	validation_0-mae:90496.63281
[714]	validation_0-mae:90408.61719
[715]	validation_0-m

[922]	validation_0-mae:74160.91406
[923]	validation_0-mae:74091.90625
[924]	validation_0-mae:74024.01562
[925]	validation_0-mae:73953.82812
[926]	validation_0-mae:73886.39844
[927]	validation_0-mae:73817.90625
[928]	validation_0-mae:73750.42188
[929]	validation_0-mae:73679.90625
[930]	validation_0-mae:73609.07031
[931]	validation_0-mae:73540.21875
[932]	validation_0-mae:73469.48438
[933]	validation_0-mae:73399.78906
[934]	validation_0-mae:73332.19531
[935]	validation_0-mae:73263.18750
[936]	validation_0-mae:73193.94531
[937]	validation_0-mae:73122.13281
[938]	validation_0-mae:73052.57812
[939]	validation_0-mae:72986.77344
[940]	validation_0-mae:72917.77344
[941]	validation_0-mae:72850.02344
[942]	validation_0-mae:72783.15625
[943]	validation_0-mae:72714.57812
[944]	validation_0-mae:72644.40625
[945]	validation_0-mae:72573.58594
[946]	validation_0-mae:72502.65625
[947]	validation_0-mae:72435.14062
[948]	validation_0-mae:72367.14062
[949]	validation_0-mae:72298.85938
[950]	validation_0-m

...

[99065]	validation_0-mae:14682.73828
[99066]	validation_0-mae:14682.72949
[99067]	validation_0-mae:14682.73438
[99068]	validation_0-mae:14682.70508
[99069]	validation_0-mae:14682.69531
[99070]	validation_0-mae:14682.67090
[99071]	validation_0-mae:14682.67481
[99072]	validation_0-mae:14682.66602
[99073]	validation_0-mae:14682.67090
[99074]	validation_0-mae:14682.66309
[99075]	validation_0-mae:14682.68848
[99076]	validation_0-mae:14682.63574
[99077]	validation_0-mae:14682.64258
[99078]	validation_0-mae:14682.66406
[99079]	validation_0-mae:14682.67969
[99080]	validation_0-mae:14682.72070
[99081]	validation_0-mae:14682.70898
[99082]	validation_0-mae:14682.69531
[99083]	validation_0-mae:14682.72070
[99084]	validation_0-mae:14682.70898
[99085]	validation_0-mae:14682.78613
[99086]	validation_0-mae:14682.79590
[99087]	validation_0-mae:14682.77539
[99088]	validation_0-mae:14682.76856
[99089]	validation_0-mae:14682.82227
[99090]	validation_0-mae:14682.82715
[99091]	validation_0-mae:14682.86133
[

[99287]	validation_0-mae:14682.93164
[99288]	validation_0-mae:14682.92676
[99289]	validation_0-mae:14682.87695
[99290]	validation_0-mae:14682.93652
[99291]	validation_0-mae:14682.88867
[99292]	validation_0-mae:14682.90039
[99293]	validation_0-mae:14682.87500
[99294]	validation_0-mae:14682.84570
[99295]	validation_0-mae:14682.82715
[99296]	validation_0-mae:14682.83691
[99297]	validation_0-mae:14682.84961
[99298]	validation_0-mae:14682.87109
[99299]	validation_0-mae:14682.84082
[99300]	validation_0-mae:14682.83008
[99301]	validation_0-mae:14682.81543
[99302]	validation_0-mae:14682.84570
[99303]	validation_0-mae:14682.84570
[99304]	validation_0-mae:14682.83008
[99305]	validation_0-mae:14682.83008
[99306]	validation_0-mae:14682.81543
[99307]	validation_0-mae:14682.81348
[99308]	validation_0-mae:14682.82324
[99309]	validation_0-mae:14682.82227
[99310]	validation_0-mae:14682.81836
[99311]	validation_0-mae:14682.80957
[99312]	validation_0-mae:14682.79102
[99313]	validation_0-mae:14682.80176
[

[99509]	validation_0-mae:14682.35059
[99510]	validation_0-mae:14682.31348
[99511]	validation_0-mae:14682.33008
[99512]	validation_0-mae:14682.29785
[99513]	validation_0-mae:14682.28223
[99514]	validation_0-mae:14682.27051
[99515]	validation_0-mae:14682.27051
[99516]	validation_0-mae:14682.27246
[99517]	validation_0-mae:14682.30273
[99518]	validation_0-mae:14682.31641
[99519]	validation_0-mae:14682.30859
[99520]	validation_0-mae:14682.28125
[99521]	validation_0-mae:14682.29102
[99522]	validation_0-mae:14682.23438
[99523]	validation_0-mae:14682.21191
[99524]	validation_0-mae:14682.22949
[99525]	validation_0-mae:14682.23926
[99526]	validation_0-mae:14682.26758
[99527]	validation_0-mae:14682.26172
[99528]	validation_0-mae:14682.26856
[99529]	validation_0-mae:14682.27734
[99530]	validation_0-mae:14682.26172
[99531]	validation_0-mae:14682.28613
[99532]	validation_0-mae:14682.28809
[99533]	validation_0-mae:14682.29590
[99534]	validation_0-mae:14682.27441
[99535]	validation_0-mae:14682.25391
[

[99731]	validation_0-mae:14681.61621
[99732]	validation_0-mae:14681.60449
[99733]	validation_0-mae:14681.61426
[99734]	validation_0-mae:14681.58203
[99735]	validation_0-mae:14681.57910
[99736]	validation_0-mae:14681.59082
[99737]	validation_0-mae:14681.58398
[99738]	validation_0-mae:14681.59766
[99739]	validation_0-mae:14681.58594
[99740]	validation_0-mae:14681.58398
[99741]	validation_0-mae:14681.60742
[99742]	validation_0-mae:14681.58691
[99743]	validation_0-mae:14681.57031
[99744]	validation_0-mae:14681.54590
[99745]	validation_0-mae:14681.54785
[99746]	validation_0-mae:14681.55273
[99747]	validation_0-mae:14681.50391
[99748]	validation_0-mae:14681.49512
[99749]	validation_0-mae:14681.48242
[99750]	validation_0-mae:14681.46777
[99751]	validation_0-mae:14681.44727
[99752]	validation_0-mae:14681.41309
[99753]	validation_0-mae:14681.44727
[99754]	validation_0-mae:14681.45703
[99755]	validation_0-mae:14681.46875
[99756]	validation_0-mae:14681.50391
[99757]	validation_0-mae:14681.48633
[

[99953]	validation_0-mae:14681.16309
[99954]	validation_0-mae:14681.17773
[99955]	validation_0-mae:14681.17090
[99956]	validation_0-mae:14681.20410
[99957]	validation_0-mae:14681.22461
[99958]	validation_0-mae:14681.23633
[99959]	validation_0-mae:14681.26562
[99960]	validation_0-mae:14681.26367
[99961]	validation_0-mae:14681.22949
[99962]	validation_0-mae:14681.23242
[99963]	validation_0-mae:14681.23828
[99964]	validation_0-mae:14681.22754
[99965]	validation_0-mae:14681.23633
[99966]	validation_0-mae:14681.23926
[99967]	validation_0-mae:14681.27734
[99968]	validation_0-mae:14681.27539
[99969]	validation_0-mae:14681.26074
[99970]	validation_0-mae:14681.24512
[99971]	validation_0-mae:14681.23144
[99972]	validation_0-mae:14681.21777
[99973]	validation_0-mae:14681.19727
[99974]	validation_0-mae:14681.19043
[99975]	validation_0-mae:14681.20019
[99976]	validation_0-mae:14681.17676
[99977]	validation_0-mae:14681.18164
[99978]	validation_0-mae:14681.19141
[99979]	validation_0-mae:14681.19531
[

In [37]:
submission = xgb.predict(clean_X_test)
#saving test predictions to file
output = pd.DataFrame({'Id' : X_test.index,
                       'SalePrice' : submission})
output.to_csv('submission4.csv', index=False)

In [35]:
clean_X_test.index

RangeIndex(start=0, stop=1459, step=1)

In [36]:
X_test.index

Int64Index([1461, 1462, 1463, 1464, 1465, 1466, 1467, 1468, 1469, 1470,
            ...
            2910, 2911, 2912, 2913, 2914, 2915, 2916, 2917, 2918, 2919],
           dtype='int64', name='Id', length=1459)